## X-ray grating spectra offer diagnostics that X-ray low-res spectra do not

<center><img src="images/OVII_levels.jpg" alt="TW Hya is surrounded by a disk and shows a high ratio of f/i in the OVII triplet, while a disk-less comparison sar does not." width="400"/></center>

- densities
- temperatures
- ionization states
- velocities
- absorption lines
- ...

## Grating data from TW Hya

In [ ]:
import IPython
IPython.display.IFrame("https://cda.harvard.edu/chaser/", width=800, height=600)

### Download the data

In [ ]:
from ciao_contrib import runtool as rt
from ciao_contrib.cda.data import download_chandra_obsids

In [ ]:
# This downloads > 4 GB of data
# It it takes a while... (15 min on my WiFi)
download_chandra_obsids([13250])


<div style="background-color:#f29696">
<h3>Aside: Installing additional Python packages into the CIAO environment</h3>
I like to use <a href="https://www.astropy.org">astropy</a> for manipulating tables and image stretching and plotting. There is a similar package (pycrates) that is distributed as part of CIAO, but I just don't know it as well. The beauty of the Python/Conda environment is that we can install additional packages pretty easily.

And while we are at it, let's install <a href="https://docs.bokeh.org/en/latest/">bokeh</a>, too. We'll use it with Sherpa later.
</div>

In [ ]:
!pip install astropy
!pip install bokeh

### A first look

In [ ]:
from astropy.table import Table
from astropy.visualization import PercentileInterval, LogStretch, imshow_norm
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import numpy as np

evt = Table.read('13250/primary/acisf13250N003_evt2.fits.gz', hdu=1)
image = np.histogram2d(evt["x"], evt["y"], bins=[1000, 1000])

In [ ]:
def plot_annotate_13250(evt, image):
    fig, ax = plt.subplots(figsize=(10, 4))
    im, norm = imshow_norm(
        image[0],
        ax,
        origin="lower",
        cmap="hot",
        interpolation="nearest",
        interval=PercentileInterval(99.999),
        stretch=LogStretch(),
        extent=[image[2][0], image[2][-1], image[1][0], image[1][-1]],
    )

    for i in range(6):
        x_corner = 950 + i * 1024 * np.sin(np.radians(-evt.meta["ROLL_PNT"]))
        y_corner = 2900 + i * 1024 * np.cos(np.radians(-evt.meta["ROLL_PNT"]))
        ax.add_artist(
            mpatches.Rectangle(
                (x_corner, y_corner),
                1024,
                1024,
                angle=evt.meta["ROLL_PNT"],
                edgecolor="w",
                facecolor="none",
                ls=":",
            )
        )

    arrowprops = dict(arrowstyle="->", lw=1.5, color="white")
    bbox = dict(boxstyle="round", fc="0.8")
    kwargs = {"arrowprops": arrowprops, "bbox": bbox}
    ax.annotate("TW Hya", (4000, 3950), xytext=(4500, 3500), **kwargs)
    ax.annotate(
        "This observation reads\nout only part of the chip.",
        (3700, 3300),
        xytext=(4000, 2500),
        **kwargs,
    )
    ax.annotate("BI chip", (4300, 4250), xytext=(3000, 4500), **kwargs)
    ax.annotate("another BI chip", (2500, 3250), xytext=(1300, 3500), **kwargs)
    ax.annotate("dispersed spectrum", (3700, 3800), xytext=(1300, 4400), **kwargs)
    ax.set_title("ObsID 13250, LEGT/ACIS-S")
    return fig


In [ ]:
fig = plot_annotate_13250(evt, image)

In [ ]:
import numpy as np
x = evt["x"] - 3998.5
y = evt["y"] - 3945.5
ang = np.deg2rad(evt.meta['ROLL_PNT'])
evt['x_rotated'] = x * np.sin(ang) + y * np.cos(ang)
evt['y_rotated'] = -x * np.cos(ang) + y * np.sin(ang)

# Select a region of the image - we'll see in the plot below why I chose those numbers
src = evt[(evt["x_rotated"] > -10) & (evt["x_rotated"] < 10) & (evt["energy"] < 6000)]

In [ ]:
def plot_annotate_13250_extraction(evt):
    fig, axes = plt.subplots(figsize=(10, 6), nrows=2, sharex=True, height_ratios=[1, 1.5])

    image = np.histogram2d(evt['x_rotated'], evt['y_rotated'], 
                        bins=(np.arange(evt['x_rotated'].min(), evt['x_rotated'].max(), 5),
                                np.arange(evt['y_rotated'].min(), evt['y_rotated'].max(), 5)))
    im, norm = imshow_norm(image[0], axes[0], origin='lower', cmap='hot', interpolation='nearest',
                        interval=PercentileInterval(99.99),
                        stretch=LogStretch(),
                        extent=[image[2][0], image[2][-1], image[1][0], image[1][-1]],)
    for y0, ysize, ec in ([-80, 40, 'c'], [-10, 25, 'w'], [40, 40, 'c']):
        axes[0].add_artist(
            mpatches.Rectangle(
                (-2450, y0),
                4900,
                ysize,
                edgecolor=ec,
                facecolor="none", lw=2,
            )
        )
    axes[0].text(-2300, -70, "background", color='c', fontsize=14)
    axes[0].text(-2300, -5, "source", color='w', fontsize=14)
    axes[0].text(-2300, 50, "background", color='c', fontsize=14)
    axes[0].set_aspect(4)
    axes[0].set_xlim(-2500, 2500)

    axes[1].scatter(src["y_rotated"], src["energy"] / 1e3, c=src["tg_part"], s=5)
    axes[1].set_ylabel("energy (keV)")
    arrowprops = dict(arrowstyle="->", lw=1.5, color="k")
    bbox = dict(boxstyle="round", fc="0.8")
    kwargs = {'arrowprops': arrowprops, 'bbox': bbox}
    axes[1].annotate("0th order", (0, 5.3), xytext=(-180, 6.3), **kwargs)
    axes[1].annotate("+1 order", (400, 1), xytext=(800, 1.3), **kwargs)
    axes[1].annotate("-1 order", (-400, 1), xytext=(-1200, 1.3), **kwargs)
    axes[1].text(-2400, 5.7, "events in the source region", color='k', fontsize=14)

    fig.tight_layout()

In [ ]:
plot_annotate_13250_extraction(evt)

### Let's do this in CIAO. Or maybe we don't have to?

- Grating products in files you get from archive
- https://tgcat.mit.edu (see later talk)
- Run `chandra_repro` for point sources, standard settings.
- Run CIAO tools separately if you need to.


<div style="background-color:#f29696">
<h3>Aside: Running CIAO tools from Python</h3>

You have been using the command line to run CIAO tools. I use Python; there is no big difference.
</div>


```bash
dmcopy "bas.fits[stdevt][time=5000:5200]" out.fits clobber=yes
```

vs.

```python
from ciao_contrib import runtool as rt
rt.dmcopy("bas.fits[stdevt][time=5000:5200]", "out.fits", clobber=True)
```

or

```python
t0 = 5000
t1 = t0 + 200
rt.dmcopy(f"bas.fits[stdevt][time={t0}:{t1}]", "out.fits", clobber=True)
```

In [ ]:
from ciao_contrib import runtool as rt

root = '13250'
evt1a = f'{root}/secondary/acisf13250_000N003_evt1a.fits.gz'
evt1out = f"{root}/evt1a.fits.gz"
asol1 = f'{root}/primary/pcadf13250_000N001_asol1.fits.gz'
flt = f'{root}/secondary/acisf13250_000N003_flt1.fits.gz'
srcpos = f'{root}/src1a.fits'
evt1areg = f'{root}/evt1a.reg'
evt2 = f'{root}/evt2.fits'
pha2 = f'{root}/pha2.fits'

rt.tgdetect2(infile=evt1a, outfile=srcpos, clobber=True)
rt.tg_create_mask(infile=evt1a, outfile=evt1areg, input_pos_tab=srcpos, clobber=True)
rt.tg_resolve_events(infile=evt1a, outfile=evt1out,
                     regionfile=evt1areg, acaofffile=asol1, clobber=True)
rt.dmcopy(infile=f'{evt1out}[EVENTS][@{flt}][cols -phas]',
          outfile=evt2, opt='all', clobber=True)
rt.tgextract(infile=evt2, outfile=pha2, tg_order_list="-1,1", clobber=True)
rt.mktgresp(infile=pha2, evtfile=evt2, outroot=root, clobber=True)
            

Ignore that warning - each spectral arm covers only some of the chips.

## We can also get a zero-order spectrum


In [ ]:
rt.dmlist(f"{evt1areg}[#row=1]")

In [ ]:
rt.specextract(
    infile=f"{evt2}[tg_m=0,Null][sky=Circle(3998.26,3945.49,31.0461)]",
    outroot=f"{root}/0order",
    # Should make a background, too, but I don't want to wait too long right now.
    # bkgfile=f"{evt2}[tg_m=0,Null][sky=region(5027_bkg.reg)]",
    weight=False,
    correctpsf=True,
    clobber=True
)

## Some spectral fitting

- We could use the files we just made, or the ones we downloaded.
- Results won't be identical but very close (that's the point of using updated calibration files!).

### Which order do we use?
By default, CIAO extracts several orders, but in TW Hya only order -1 and +1 are bright enough to learn something.

For LETG/ACIS we get 6 spectra in the pha2 file -3, -2, -1, +1, +2, +3

### Should we merge spectra?
- Generally not recommended for fitting.
- But certainly useful for plotting.

In [ ]:
rt.combine_grating_spectra(infile="13250/primary/acisf13250N003_pha2.fits.gz",
        outroot='13250/', add_plusminus=True, order=1,
        arf="13250/primary/responses/*arf2.fits.gz",
        rmf="13250/primary/responses/*rmf2.fits.gz",
        clobber=True)

In [ ]:
from sherpa.astro import ui

ui.load_data(1, "13250/primary/acisf13250N003_pha2.fits.gz")
# The PHA2 file has 6 spectra that are read into ids 1 to 6.
# 1: order -3
# 2: order -2
# 3: order -1  - we want to use this
# 4: order +1  - and this one
# etc.

# Let's load effective area and responses:
ui.load_arf(3, "13250/primary/responses/acisf13250N003_Lm1_arf2.fits.gz")  
ui.load_rmf(3, "13250/primary/responses/acisf13250N003_Lm1_rmf2.fits.gz")
ui.load_arf(4, "13250/primary/responses/acisf13250N003_Lp1_arf2.fits.gz")
ui.load_rmf(4, "13250/primary/responses/acisf13250N003_Lp1_rmf2.fits.gz")

# load combined for plotting
ui.load_pha('combined', '13250/combo_leg_abs1.pha')

In [ ]:
ui.load_data('0order', '13250/0order.pi')

In [ ]:
ui.set_analysis('wave')
ui.plot_data(3)

In [ ]:
ui.notice(5.0, 25.0)
ui.group_width(4)

In [ ]:
ui.plot_data(3, yerrorbars=False, linestyle='solid', marker='None', label='order -1')
ui.plot_data(4, yerrorbars=False, linestyle="solid", marker='None', overplot=True, label='order +1')
ui.plot_data('0order', yerrorbars=False, linestyle='solid', marker='None', overplot=True, label='order 0')

In [ ]:
from sherpa import plot as shplot
from bokeh.plotting import show
from bokeh.io import output_notebook
output_notebook()

with shplot.TemporaryPlottingBackend('BokehBackend'):
    ui.plot_data(3, yerrorbars=False, linestyle='solid', marker='None')
    ui.plot_data(4, yerrorbars=False, linestyle="solid", marker='None', overplot=True)
    ui.plot_data(
        "0order", yerrorbars=False, linestyle="solid", marker="None", overplot=True
    )
    show(shplot.backend.current_fig)

In [ ]:
ui.ignore(None, None)
ui.notice(13.3, 13.9)

ui.plot_data("combined")

In [ ]:
const = ui.const1d("const")
ne9_r = ui.delta1d("Ne IX r")
ne9_r.pos = 13.45
ne9_r.pos.frozen = True
ne9_i = ui.delta1d("Ne IX i")
ne9_i.pos = 13.55
ne9_i.pos.frozen = True
ne9_f = ui.delta1d("Ne IX f")
ne9_f.pos = 13.70
ne9_f.pos.frozen = True

triplet = const + ne9_r + ne9_i + ne9_f

ui.set_source(3, triplet)
ui.set_source(4, triplet)
ui.set_source("combined", triplet)

In [ ]:
ui.set_stat('cash')
ui.fit(3, 4)

In [ ]:
ui.plot_fit("combined")

Our starting values are too far away from the best fit, so it didn't work.

And, when a model with the cash statistics falls below 0, there is trouble.

In [ ]:
for line in [ne9_r, ne9_i, ne9_f]:
    line.ampl = 0.01
    line.ampl.min = 0 

const.c0 = 0.02
const.c0.min = 0

In [ ]:
ui.fit(3, 4)

In [ ]:
ui.conf(3, 4)

In [ ]:
ui.plot_fit("combined")

ax = plt.gca()
ax.set_title('Ne IX triplet in ObsID 13250')
for line, wave in [('r', 13.45), ('i', 13.55), ('f', 13.70)]:
    ax.text(wave, 0.12, line, fontsize=16, ha='center')

In [ ]:
conf_res = ui.get_conf_results()

In [ ]:
flux_r = conf_res.parvals[1]
flux_i = conf_res.parvals[2]
flux_f = conf_res.parvals[3]
err_r = conf_res.parmaxes[1]
err_i = conf_res.parmaxes[2]
err_f = conf_res.parmaxes[3]
fi2r = (flux_f + flux_i) / flux_r
f2i = flux_f / flux_i

# I know this is not statistically correct, but in this tutorial I really just want
# to focus on grating data.
# You can improve this as a homework assignment  ;-)

err_f2i = np.sqrt(
    (err_f / flux_f) ** 2 + (err_i / flux_i) ** 2
)
err_fi2r = np.sqrt(
    (err_f / flux_r) ** 2 + 
    (err_i / flux_r) ** 2 + 
    ((flux_f + flux_i) * err_r/ flux_r**2) ** 2
)

print(f"flux ratio f/i: {f2i:.3f} +/- {err_f2i:.3f}")
print(f"flux ratio (f+i)/r: {fi2r:.3f} +/- {err_fi2r:.3f}")

### Now, we can determine the plasma density from the line ratio

- Calculated expected line ratios with [CHIANTI database](https://www.chiantidatabase.org/)
- Used the [chiantiPy](https://chiantipy.readthedocs.io/en/latest/)
- Saved in a datafile we're going to read in
- (A tutorial on chiantiPy is out of scope, but talk to me if you need it.)

<center><img src="images/OVII_levels.jpg" alt="TW Hya is surrounded by a disk and shows a high ratio of f/i in the OVII triplet, while a disk-less comparison sar does not." width="400"/></center>

In [ ]:
ne_9_emissivity = np.load("ne9_emiss.npz")

In [ ]:
ne_9_emissivity["e_hea"].shape, ne_9_emissivity["logtemp"].shape, ne_9_emissivity["logdens"].shape
emiss_f2i = ne_9_emissivity["e_f"] / ne_9_emissivity["e_i"]
emiss_fi2r = (ne_9_emissivity["e_f"] + ne_9_emissivity["e_i"]) / ne_9_emissivity["e_hea"]


In [ ]:
fig, ax = plt.subplots()

for i, logdens in enumerate(ne_9_emissivity["logdens"]):
    ax.plot(emiss_f2i[:, i], emiss_fi2r[:, i], color="0.8")
    ax.text(emiss_f2i[:, i][0], emiss_fi2r[:, i][0], f"{logdens:.1f}",
        rotation=90, ha='center')
for i, logtemp in enumerate(ne_9_emissivity["logtemp"]):
    ax.plot(emiss_f2i[i, :], emiss_fi2r[i, :], color="0.8")
    ax.text(min(emiss_f2i[i, :][0], 4), emiss_fi2r[i, :][0], f"{10**(logtemp-6):.0f} MK", 
            fontsize=10)

ax.set_xlim(0, 4)

ax.errorbar(f2i, fi2r, xerr=err_f2i, yerr=err_fi2r,
    fmt="o", color="k", label="ObsID 13250")
ax.set_xlabel("f/i")
ax.set_ylabel("(f+i)/r")
_ = ax.set_title("Density and temperature from Ne IX triplet")


## Repeat the process for the other datasets

- Time is short, so I'll just show you the answer.

<center><img src="images/Chandra_n_t.jpg" alt="Veiling lightcurve" width="600"/></center>

- So, density and temperature in the emission region are correlated.
- What does that mean?
  - not sure yet, that's why it's called research
  - Dense hot core and less dense cooler outer region?
  - Only if rate and geometry are right, we see the lines from the core.
- How to test?
  - Measure lines formed at different densities and temperature (e.g. O VII triplet)
  - Get accretion rate from line amplitude
  - and compare to rate from optical around that time

## Conclusion

### Science
- Stars from in dense clouds of gas and dust.
- They accrete mass from their disks, which powers accretion shocks...
- ... and those shocks in turn ionize the disk, shaping how accretion proceeds.
- X-ray grating spectra are a powerful tool to study accretion in young stars
- We see high density -> accretion shock signature.
- Temperature and density are correlated, but not clear why yet.

### Chandra gratings

- HETG (HEG + MEG = 4 spectral arms)
- LETG (2 spectral arms)
- either used with ACIS (energy sorting, 0 order spectrum) or HRC (can detect soft photons)
- special topics not covered
  - pile-up
  - CC mode
  - extended sources
  - overlapping sources
- Point source spectra are already included in data products.